In [ ]:
import math as m
import sys
import io
from urllib.request import urlopen
import numpy as np
import scipy as sp
import scipy.io.wavfile as wavfile
import soundfile as sf
from imageio import imread
import matplotlib
import matplotlib.pyplot as plt
import matplotlib.animation as anim
from mpl_toolkits.mplot3d import Axes3D
import IPython
import IPython.display as ipd
import ipywidgets as ipw

# Seção 2.3: Um exemplo motivacional

## Figura 2.2 - Sinal analógico no domínio do tempo

In [ ]:
T = 1
N = 128
t = np.arange(0, T, 1/N)
doispi = 2 * m.pi
x = 2*np.cos(doispi*5*t) + 0.8*np.sin(doispi*12*t) + 0.3*np.cos(doispi*47*t)
print("Primeiras 10 amostras do sinal: ",np.round(x[0:10],3))
plt.plot(t,x); plt.xlabel("t"); plt.ylabel("x(t)")
plt.show()

In [ ]:
X = np.fft.fft(x)
c = X / N
print(np.round(c,2))

### Mostra coeficientes não-nulos

In [ ]:
eps = 1e-8
for k, ck in np.ndenumerate(c):
    if abs(ck) > eps: print ("c({0}) = {1:.2f}".format(k,ck)) 

### Mostra energia em cada componente

In [ ]:
print("E(x)\t=\t{0:.2f}".format(np.linalg.norm(x)**2))
print("--------------------------")
E = N * abs(c)**2
for (k,), Ek in np.ndenumerate(E):
    if abs(Ek) > eps: print("E({0})\t=\t{1:.2f}".format(k,Ek))
print("--------------------------")
print("E(c)*N\t=\t{0:.2f}".format(sum(E)))

## Figuras 2.3 e 2.4 - Espectro do sinal de exemplo

### Espectro centralizado na frequência 0

In [ ]:
plt.plot(np.arange(N) - N/2, np.roll(E, int(N/2)))
plt.xlabel("k"); plt.ylabel("E(k)")
plt.show()

### Espectro no intervalo [0, N-1]

In [ ]:
plt.plot(E); plt.xlabel("k"); plt.ylabel("E(k)")
plt.show()

## Figura 2.5 - Espectro com pares de frequências $\pm\ f_k$ agrupadas

In [ ]:
E[1:int(N/2)-1:1] *= 2
plt.plot(E[0:int(N/2)]); plt.xlabel("k"); plt.ylabel("E(k)+E(-k)")
plt.show()

## Figura 2.6 - Sinal ruidoso e sinal filtrado

In [ ]:
# Elimina "altas frequências" (acima de 40 Hz)
Y = X
Y[40:N-40:1] *= 0
y = np.real(np.fft.ifft(Y))
plt.subplot(1, 2, 1);plt.title("Sinal original");plt.plot(t,x)
plt.subplot(1, 2, 2);plt.title("Sinal filtrado");plt.plot(t,y)
plt.show()

# Seção 2.4: A DFT unidimensional

## Figura 2.7 - Espectro do sinal com rebatimento (aliasing)

In [ ]:
N2 = N/2
tt = np.arange(0, 1, 1/N2)
xx = 2*np.cos(doispi*5*tt) + 0.8*np.sin(doispi*12*tt) + 0.3*np.cos(doispi*47*tt)
plt.plot(tt,xx); plt.title("Sinal amostrado a 64 Hz"); plt.show()

In [ ]:
XX = np.fft.fft(xx)
cc = XX / (N2)
EE = (N/2) * abs(cc)**2
plt.plot(EE[0:int(N/4)]); plt.title("Energia do sinal reamostrado"); plt.show()
f = 47
print("Componente de {0} Hz rebatida = {1} Hz".format(f,f%N2 if f%N2<=N2/2 else N2-f%N2))

## Figuras 2.8 - 2.10 - Pulsos quadrados

In [ ]:
N = 256
t = np.arange(N)
R = [50, 10, 2 ,1]
for r in R:
    x = np.zeros(N)
    x[0:r:1] = 1
    plt.subplot(1, 2, 1)
    plt.plot(x)
    X = np.fft.fft(x)
    c = X / N
    E = N * abs(c)**2
    plt.subplot(1, 2, 2)
    plt.plot(np.arange(N) - N/2, np.roll(E, int(N/2)))
    plt.show()
fig = plt.figure()
plt.plot()
plt.axis('off')
plt.show()

## Figura 2.11 - Sinal aleatório e sua DFT

In [ ]:
N = 2**8; t = np.arange(N)
a = -1; b = 1
x = np.random.rand(N) * (b - a) + a  #amostra valores de uma distribuição uniforme em [a, b)
sigma = (b - a) / m.sqrt(12)   #desvio padrão da variável aleatória com distribuição uniforme em [a,b)

In [ ]:
#referência: Time Series Analysis and Its Applications: With R Examples (Robert H. Shumway, David S. Stoffer)
plt.subplot(4, 2, 1); plt.title("Sinal temporal"); plt.plot(t, x)
shifted_range = np.arange(N) - N/2

#uma sequência de variáveis aleatórias descorrelacionadas com variância sigma^2 terá densidade espectral constante igual a sigma^2 (ex 4.4 do Sumway & Stoffer)
plt.subplot(4, 2, 2); plt.title("Densidade espectral"); plt.plot(shifted_range, (sigma ** 2) * np.ones(N) )

X = np.fft.fft(x)
c = X / m.sqrt(N) # coeficentes da DFT (eq. 4.18 do Shumway & Stoffer)
E = abs(c)**2  #peridograma (energia) do sinal  (eq. 4.20 do Shumway & Stoffer): seria o mesmo obtido fazendo c=X/N; E = N*abs(c)**2
shifted_E = np.roll(E, int(N/2)) #faz um "shift à direita" de  int(N/2) posições em E

#Ponto positivo:quando N tende a infinito, a esperança (valor médio) do periodograma tende à densidade espectral (eq. 4.20 do Shumway & Stoffer)
#-> Logo, o periodograma é um estimador assintoticamente não viesado da densidade espectral
#Problema: a variância do periodograma não diminui conforme N aumenta (ver prop. 4.4 e exemplo 4.10 do Shumway & Stoffer)
#-> Logo, o periodograma não é um estimador assintoticamente "estável" densidade espectral
plt.subplot(4, 2, 3); plt.title("Periodograma (energia)"); plt.plot(shifted_range, shifted_E)

#Alternativa: tentar diminuir a variância através da suavização do periodograma (ver seção 4.5 do Shumway & Stoffer)
#-> Uma opção é usar médias móveis, com uma janela deslizante de largura L 
def smooth(a, L=3, kernel='daniell', repeat=False):
    if L % 2 != 1 or L <= 1 or not isinstance(L, int): #L deve ser ímpar, inteiro e >= 3
        raise ValueError("Parameter 'L' (%d) must be an odd integer greater or equal to 3" % (L))  
    if L > len(a):
        raise ValueError("Parameter 'L' (%d) is too large to apply kernel again" % (L))              
        
    weights = False #pesos da media
    output = False  #saida (sinal suavizado)
    mode = 'valid' #faz a media ponderada apenas quando a janela estiverem totalmente contida no sinal 
    if kernel == 'daniell':
        weights = np.ones(L)/L #vetor de pesos de tamanho L, com cada elemento igual a 1/L 
    elif kernel == 'modified.daniell':
        w1 = 0.5 / (L-1) #peso das pontas
        w2 = 2 * w1 #peso no interior da janela
        weights = np.concatenate([[w1],np.ones(L-2)*w2,[w1]])
    else:
        raise ValueError("Parameter 'kernel' (%s) must be '' or ''" % (kernel))  
    
    output = np.convolve(a, weights, 'valid')
    
    if repeat:
        if L > len(output):
            raise ValueError("Parameter 'L' (%d) is too large to apply the kernel again" % (L))              
        output = np.convolve(output, weights, 'valid')
        
    return output

L = 3
smoothed_E = smooth(shifted_E,L,kernel='daniell', repeat=False)
plt.subplot(4, 2, 4); plt.title("Per. suavizado (Daniell)"); plt.plot(shifted_range[int(np.floor(L/2)):-int(np.floor(L/2))], smoothed_E)

smoothed_E = smooth(shifted_E,L,kernel='modified.daniell', repeat=False)
plt.subplot(4, 2, 5); plt.title("Per. suavizado (Daniell modif.)"); plt.plot(shifted_range[int(np.floor(L/2)):-int(np.floor(L/2))], smoothed_E)

smoothed_E = smooth(shifted_E,L,kernel='daniell', repeat=True)
plt.subplot(4, 2, 6); plt.title("Per. suavizado (Dan. repetido)"); plt.plot(shifted_range[int(2*np.floor(L/2)):-int(2*np.floor(L/2))], smoothed_E)

smoothed_E = smooth(shifted_E,L,kernel='modified.daniell', repeat=True)
plt.subplot(4, 2, 7); plt.title("Per. suavizado (Dan. modif. repetido)"); plt.plot(shifted_range[int(2*np.floor(L/2)):-int(2*np.floor(L/2))], smoothed_E)

plt.tight_layout()
plt.show()

## Figura 2.12: Sinal de sino e sua DFT

In [ ]:
# para abrir arquivo wav de url:
url="http://static1.grsites.com/archive/sounds/bells/bells004.wav"
x, rate = sf.read(io.BytesIO(urlopen(url).read()))
# esse arquivo tem uma codificação estranha, com uma média muito maior do que 0: corrige
x = x-np.mean(x,0)
# para abrir arquivo wav local:
# rate, x = wavfile.read('bell.wav')
plt.plot(x)
plt.show()
ipd.Audio(x.T, rate=rate)

In [ ]:
X = np.fft.fft(x[:,0])
N = len(x)
E = 2*abs(X[0:int(N/2):1])**2/N
plt.subplot(1, 2, 1); plt.plot(np.arange(N/2) *rate/N, E); plt.title("Espectro de Energia")
plt.subplot(1, 2, 2); plt.plot(np.arange(6000) *rate/N, E[0:6000:1]); plt.title("Espectro de Energia (detalhe)")
plt.show()

### Exemplo de remoção de componentes mais "fracas"

In [ ]:
Y = X.copy()
C = 0.1 * abs(Y).max()
for val in np.nditer(Y, op_flags=['readwrite']):
    if abs(val) < C:
        val[...] = 0
rex = np.real(np.fft.ifft(Y))
EY = 2*abs(Y[0:int(N/2):1])**2/N
plt.subplot(1, 2, 1); plt.plot(rex); plt.title("Sinal ressintetizado")
plt.subplot(1, 2, 2); plt.plot(np.arange(N/2) *rate/N, EY); plt.title("Espectro ressintetizado")
plt.show()

In [ ]:
ipd.Audio(rex, rate=rate)

# Seção 2.5: Propriedades da DFT

# Seção 2.6: Transformada Rápida de Fourier

# Seção 2.7: A DFT bidimensional

# Figura 2.13 - Imagem e várias apresentações da DFT

In [ ]:
url = "http://sutherncharm.files.wordpress.com/2009/09/double-ferris.jpg"
M = imread(urlopen(url).read())
plt.subplot(1, 2, 1); plt.title("Imagem original"); plt.imshow(M)
N = np.fft.fft2(M,axes=(0,1)); absN = np.abs(N)
plt.subplot(1, 2, 2); plt.title("Espectro"); plt.imshow(255 * absN / absN.max())
plt.show()
halfheight, halfwidth = int(absN.shape[0]/2), int(absN.shape[1]/2)
shiftN = np.roll(absN, (halfheight,halfwidth), axis=(0,1))
plt.subplot(1, 2, 1); plt.title("Espectro centralizado em (0,0)"); plt.imshow(255 * shiftN / shiftN.max() )
Nlog = np.log(1 + shiftN)
maxi, mini = Nlog.max(), Nlog.min(); Nshow = (Nlog - mini) / (maxi - mini)
plt.subplot(1, 2, 2); plt.title("Log-Espectro normalizado"); plt.imshow(Nshow)
plt.show()
C = 0.001 * absN.max()
for val in np.nditer(N, op_flags=['readwrite']):
    if abs(val) < C:
        val[...] = 0
reM = np.round(np.real(np.fft.ifft2(N, axes=(0,1))))
reMin, reMax = reM.min(), reM.max()
reMshow = (reM - reM.min())/ (reM.max() - reM.min())
plt.title("Ressíntese após compressão"); plt.imshow(reMshow)
plt.show()
fig = plt.figure()
plt.plot()
plt.axis('off')
plt.show()

# Figura 2.14: Imagem artificial e visualizações da DFT

In [ ]:
O = np.zeros((300,300,3)); O[100:150,100:110,0:3] += 1
plt.subplot(1, 2, 1); plt.title("Imagem original"); plt.imshow(O)

N = np.fft.fft2(O,axes=(0,1)); absN = abs(N)
plt.subplot(1, 2, 2); plt.title("Espectro"); plt.imshow(absN/ absN.max())
plt.show()

halfheigth, halfwidth = int(absN.shape[0]/2), int(absN.shape[1]/2)
shiftN = np.roll(absN, (halfheigth, halfwidth), axis=(0,1))
plt.subplot(1, 2, 1); plt.title("Espectro centralizado em (0,0)"); plt.imshow(shiftN / shiftN.max())

Nlog = np.log(1 + shiftN)
maxi, mini = Nlog.max(), Nlog.min()
Nshow = (Nlog - mini) / (maxi - mini)
plt.subplot(1, 2, 2); plt.title("Log-Espectro normalizado"); plt.imshow(Nshow)
plt.show()

fig = plt.figure()
plt.plot()
plt.axis('off')
plt.show()